In [12]:
import os
import time
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
from tqdm import tqdm
import math

from collections import Counter
from imblearn.over_sampling import RandomOverSampler

from sklearn.model_selection import train_test_split
from sklearn import metrics

from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.layers import Dense, Input, LSTM, Embedding, Dropout, Activation, CuDNNGRU, Conv1D
from keras.layers import Bidirectional, GlobalMaxPool1D
from keras.models import Model
from keras import initializers, regularizers, constraints, optimizers, layers

from TextPreprocessor import *
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Load the data

In [4]:
train = pd.read_csv("../data/train.csv")
test = pd.read_csv("../data/test.csv")
print("Training data shape : ",train.shape)
print("Testing data shape : ",test.shape)

Training data shape :  (1306122, 3)
Testing data shape :  (56370, 2)


In [5]:
# check sample submission
sub = pd.read_csv("../data/sample_submission.csv")
sub.head()

qid  prediction
0  00014894849d00ba98a9           0
1  000156468431f09b3cae           0
2  000227734433360e1aae           0
3  0005e06fbe3045bd2a92           0
4  00068a0f7f41f50fc399           0

In [6]:
train.head()

qid                                      question_text  \
0  00002165364db923c7e6  How did Quebec nationalists see their province...   
1  000032939017120e6e44  Do you have an adopted dog, how would you enco...   
2  0000412ca6e4628ce2cf  Why does velocity affect time? Does velocity a...   
3  000042bf85aa498cd78e  How did Otto von Guericke used the Magdeburg h...   
4  0000455dfa3e01eae3af  Can I convert montra helicon D to a mountain b...   

   target  
0       0  
1       0  
2       0  
3       0  
4       0

In [7]:
# check missing
print(train.shape[0], train.dropna().shape[0])
# there is no missing in training

# convert type 
train.question_text = train.question_text.astype(str)
train.target = train.target.astype(int)

1306122 1306122


### EDA 

In [9]:
# check balance of class
import seaborn as sns
ax = sns.countplot(x="target", data=train)
# very imbalance data set 

In [103]:
# have a look at the target cases:
for text in train.loc[train.target ==1][["question_text"]].values:
    print(text[0])

Has the United States become the largest dictatorship in the world?
Which babies are more sweeter to their parents? Dark skin babies or light skin babies?
If blacks support school choice and mandatory sentencing for criminals why don't they vote Republican?
I am gay boy and I love my cousin (boy). He is sexy, but I dont know what to do. He is hot, and I want to see his di**. What should I do?
Which races have the smallest penis?
Why do females find penises ugly?
How do I marry an American woman for a Green Card? How much do they charge?
Why do Europeans say they're the superior race, when in fact it took them over 2,000 years until mid 19th century to surpass China's largest economy?
Did Julius Caesar bring a tyrannosaurus rex on his campaigns to frighten the Celts into submission?
In what manner has Republican backing of 'states rights' been hypocritical and what ways have they actually restricted the ability of states to make their own laws?
Would Europeans continue to participate in

Why does the continuity of real numbers in mathematics not strictly exist but was made artificially and deliberately existing by so many alleged top most genius historical figures in mathematicians for too narrow self purposes?
Do Christians think that revenge/murder/jealousy are good things and freedom/individuality/wisdom are bad things?
Why does Liberia want to be the 51st states of the United States of America instead of being an independent country?
If AMU is a central university and not a Muslim university, then how can they ban entry of students for blasphemy? Are Muslims above Indian law? Do Muslims have respect for Indian Constitution as they want action according to Sharia?
I'm 19 and my mother is still giving me oral sex every day. Is it time for her to stop?
Why is India slowly becoming unsafe country for Hindus? Why are Hindus being discriminated, insulted, and humiliated every day?
Why are some Scottish people so loyal to the British crown, and not rebellious and independ

Does the fact that Trump watches a "gorilla channel" consisting of footage of black people fighting each other show the true extent of his racism?
Isn’t "House on Fire" by Sia not a nice Palestinian song?
At which age do most women start getting double penetrated? What are some statistics?
Is Sean Hannity a lying partisan hack? How can anyone take anything he says seriously?
Why does the RSS hate Dalits so much?
Why don't French Muslims rise up against France?
How do I download the Blue Whale challenge on Android?
When will somebody land on the moon for real?
Then who we complain to about the rigged search engine? When I type White American Inventors I get photos of Blacks and even Muslim Clock Boy.
Are you a pro-pineapples pizza or are you sane?
“Why did the U.S. save England in WWII? Why did our grandfathers shed their blood to save a staging area?” Why did Quora delete these questions and my answer?
Can we give "walkover" to Pakistan in Champions Trophy considering terror attacks an

How do I psychologically crush my girlfriend for looking at other men in the street?
Why are white people smarter?
If Jabba had captured Luke Skywalker, would he have had him castrated?
Why has India been a super illiterate country in the world?
Will a Muslim girl in todays time love and marry a Hindu guy in India? Does she has the guts to accept Hinduism?
Why don't real men choose their words lightly? Is it true, why or why not?
Why do women complain about the wage gap when they extort more than enough to compensate for this in "child" support?
Are men from Islam so out of control that their women have to cover themselves totally? Do they get aroused on seeing women outside Islam who wear normally?
Are HK girls materialistic?
Why do Chinese hate Koreans and Japanese?
Why does Tennessee smell bad?
Can I have sex with my mother?
Is it normal to walk naked at night?
Is a 9 inch penis big for a 14 year old?
Why do 128 countries teach a lesson to the US President, on the issue of Jerusalem

Why won't mainstream media comment on the good things Trump does, and why won't they admit they are liberal-biased and ran by the democratic party?
Do women like to poo?
What are the views of the Brahmin-haters of Maharashtra on Bajirao I and Bal Gangadhar Tilak?
Why do people ask such stupid questions on this website?
WhyBlack people only blame the white people for their slavery and not blaming the Arab too
Is there currently anyone on Quora who advocates the legalization of pedophilia? In their worldview, would you need the parents consent to marry/have sex with a 9 year old? Would the pedophile still find the 9 year old attractive once they grow up?
Why Hindu brothers killing Muslim brothers?
Since paper is made from trees, will planting more of them help defeat Dwayne Johnson in the 2020 election? Does this mean global warming just a sham?
Why does the BJP & a certain section of the media have Rahul phobia?
Do South Indians realize that they are the "Asuras" mentioned in the Vedas 

...

Do you believe that East and Southeast Asians even South Asians have a deep love affair with the Brexiting Britain than the rest of Mainland Europe that contains of France, Germany, Belgium, Netherlands, Luxembourg, Italy, Spain, etc.?
Which is the bigger enemy of the USA, front stabbing China or backstabbing European countries?
Why did Mustafa Kemal Ataturk persecute Christians?
Why do Mediterranean people think they are white? When they look Latino? Are they being false to themselves?
How did America miss the Middle East in four decades? And how did the illiterate Shiite mullahs control the Middle East? Given the fact that Iran's mullahs had no political power forty years ago.?
Do popular Quorans after reaching 10K followers become man eaters?
Okay so I was in the shower and I looked at my erect penis and then decided to measure it using my iPhone 7 and my penis is just slightly longer, for the women how’s that compare to other penises you’ve encountered?
It’s been nearly 24 hours si

In India, would you not discourage your wife to wear short skirts, expose her legs, and expose her cleavage when she goes shopping?
Have there ever been backpackers that weren't white?
Should Pakistan and, Bangladesh attack India to get Kashmir and West Bengal from India?
Do you believe that the original Americans are black while white were slaves which were dropped here for punishment?
Why don't Africans spend time turning back the desert instead of shooting their neighbors due to primitive tribalism?
Quora for God sake when will you stop all the nonsense about the royal wedding, I am fedup of reading the topics which I have already muted?
Why do Muslims get offended when I point out the fact that Muhammad had 11 wives and one was 9 years old? It’s a fact.
Why do people start crying in the hospital itself when a girl is born? Do they improve later?
What are some examples of atrocities committed by the Muslims against the Hindus?
If Jews were at risk during WW2, could they not have cha

As an Indian, how can I get married with my own sister, especially when we both have a great wish of it?
Would Putin not releasing the material damaging to Clinton (if known) have been seen as helping Clinton?
Why didn't Ravish Kumar and Arvind Kejriwal didn't say a word against harassment of Dangal actress Zaira Wasim?
Researchers now say that paedophiles are born that way just like for transgenders and homosexuals. If parents allow their children to choose their gender, how do we know a child isn't a teleiophile? And why should we stop them if they both want it?
Are there Americans who are in the UK (especially England), who don't believe that carrying weapons in self defense is okay? Have they gotten rid of the idea that it is okay?
How Much estrogen is produced daily in the Californian senate? And why haven't you guys stopped DRUMPF yet?
Are those YouTubers or social media heavy users considered "attention seekers" who feel constantly insecure about not getting attention?
Can I get

Why is it in America if you do not like people that violate the law according to the Democratic party you are automatically a racist because according to them if you do not like illegal immigrants because they are violating the law you are racist?
I've removed all pink from my son's room to stop him from being gay, what success rate does this practice carry?
Can I marry mu bua's daughter?
Why are Indians bad employers?
No bell, no speaker, but louspeaker at mosque. Why do Muslims interfere with Hindu worship?
Why do Telugu Brahmins envy Viswakarmas?
Should whole world team up to warn America to impeach trump or whole world go on war against America?
Obama is a Christian. Trump is an atheist. Why do nearly all atheists I know hate Trump?
Why South Indian girls are so boring when it comes to relationship?
Is anyone else sick of people telling how much Sachin Tendulkar was better than Virat Kohli?
Why isn't there any qualification criteria or entrance exam (for fooling Indians) to be a MP

Can an animal get a human pregnant?
Are women more blank than men?
Did you know that people who don't believe in Christ are bad people?
Why in Quora majority of persons are either supporters of BJP or AAP and except few there is no popular Quoran supporter of congress?
Science can see that BIID and transgender are essentially the same (see link).So why don't people in society respect the plight of the transabled the same as they do for transgendered?
Rose McGowan settled after she was raped by Harvey Weinstein, but if she'd gone to the police instead, couldn't she have saved more women going through the same ordeal?
Can Chinese propagandists on Quora not tell how obvious it is they are exactly that?
Why Indian lady cheats her husband?
I earn money in the US and send my savings back home to charities in Pakistan, one of whom work in converting Christians back to Islam. How do white people feel about that?
If someone took a piss why would they take a shit?
Why do so many people hate Repu

In [17]:
# Over-sample the data to balance the cases
X = train.question_text.values
y = train.target.values
print(X.shape, y.shape)

(1306122,) (1306122,)


### Feature engineering

Customize Tokenization:

- remove numbers
- remove punctuations
- turn all tokens to lowercase
- remove stopwords 
- lemmatizations
- stemming 

- reference:  https://towardsdatascience.com/hacking-scikit-learns-vectorizers-9ef26a7170af

In [20]:
# check the tokenization results
for doc in train.loc[train.target ==1][["question_text"]].values[:100]:
    print(doc[0])
    print(my_tokenizer(doc[0]))

Has the United States become the largest dictatorship in the world?
['unit', 'state', 'becom', 'largest', 'dictatorship', 'world']
Which babies are more sweeter to their parents? Dark skin babies or light skin babies?
['babi', 'sweeter', 'parent', 'dark', 'skin', 'babi', 'light', 'skin', 'babi']
If blacks support school choice and mandatory sentencing for criminals why don't they vote Republican?
['black', 'support', 'school', 'choic', 'mandatori', 'sentenc', 'crimin', 'vote', 'republican']
I am gay boy and I love my cousin (boy). He is sexy, but I dont know what to do. He is hot, and I want to see his di**. What should I do?
['gay', 'boy', 'love', 'cousin', 'boy', 'sexi', 'dont', 'know', 'hot', 'want', 'see', 'di']
Which races have the smallest penis?
['race', 'smallest', 'peni']
Why do females find penises ugly?
['femal', 'find', 'peni', 'ugli']
How do I marry an American woman for a Green Card? How much do they charge?
['marri', 'american', 'woman', 'green', 'card', 'much', 'charg']

['could', 'presid', 'sign', 'execut', 'order', 'ban', 'nra', 'make', 'campaign', 'contribut', 'level']
Why Chinese people are always not welcome in all countries?
['chines', 'peopl', 'alway', 'welcom', 'countri']
Who will win in video game battle: Adam d angelo vs Kim kardasian?
['win', 'video', 'game', 'battl', 'adam', 'angelo', 'v', 'kim', 'kardasian']
Why do Swedish people wear American clothes like Levi's then say Americans don't have fashion?
['swedish', 'peopl', 'wear', 'american', 'cloth', 'like', 'levi', 'say', 'american', 'fashion']
What is the average IQ of people who don't believe in the flat Earth?
['averag', 'iq', 'peopl', 'believ', 'flat', 'earth']
Do Muslims understand that when they think they get 22 virgins when they blow themselves up, the Koran translation is actually wrong? It translates to 22 raisins, because raisins were a rare delicacy back then.
['muslim', 'understand', 'think', 'get', 'virgin', 'blow', 'koran', 'translat', 'actual', 'wrong', 'translat', 'raisin

['transgend', 'sent', 'prison', 'trump']
Why are men still hung up on being the initiator or pursuer with dating when that just sounds like a creepy way of viewing women as prey in the animal kingdom?
['men', 'still', 'hung', 'initi', 'pursuer', 'date', 'sound', 'like', 'creepi', 'way', 'view', 'woman', 'prey', 'anim', 'kingdom']
Why is it that some people who ask to follow me haven't asked or answered any questions? Some only have one or two followers. Some have lots of followers and I can’t understand why. What manner of Quoran is this? Are they monitors?
['peopl', 'ask', 'follow', 'ask', 'answer', 'question', 'one', 'two', 'follow', 'lot', 'follow', '’', 'understand', 'manner', 'quoran', 'monitor']
Do Mongolian Gypsies (Turks) want to join the EU, or is it just the government that wants to join desperately?
['mongolian', 'gypsi', 'turk', 'want', 'join', 'eu', 'govern', 'want', 'join', 'desper']
At what point do you simply accept that Trump is too evil and/or crazy to be President an

In [29]:
X[:1000]

array([['How did Quebec nationalists see their province as a nation in the 1960s?'],
       ['Do you have an adopted dog, how would you encourage people to adopt and not shop?'],
       ['Why does velocity affect time? Does velocity affect space geometry?'],
       ['How did Otto von Guericke used the Magdeburg hemispheres?'],
       ['Can I convert montra helicon D to a mountain bike by just changing the tyres?'],
       ['Is Gaza slowly becoming Auschwitz, Dachau or Treblinka for Palestinians?'],
       ['Why does Quora automatically ban conservative opinions when reported, but does not do the same for liberal views?'],
       ['Is it crazy if I wash or wipe my groceries off? Germs are everywhere.'],
       ['Is there such a thing as dressing moderately, and if so, how is that different than dressing modestly?'],
       ['Is it just me or have you ever been in this phase wherein you became ignorant to the people you once loved, completely disregarding their feelings/lives so you get 

In [30]:
# use customized tokenizer with sklearn Vectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer(tokenizer=my_tokenizer)
X = vectorizer.fit_transform(X[:1000])

In [31]:
vectorizer.get_feature_names()

['aa',
 'aadhar',
 'abandon',
 'abil',
 'abl',
 'abolish',
 'aborigin',
 'abort',
 'abroad',
 'absent',
 'absolut',
 'absorb',
 'abus',
 'academ',
 'accent',
 'accept',
 'access',
 'accomplish',
 'accord',
 'account',
 'accur',
 'accus',
 'acer',
 'achiev',
 'across',
 'act',
 'action',
 'activ',
 'activa',
 'activist',
 'actor',
 'actual',
 'acv',
 'ad',
 'adam',
 'add',
 'addison',
 'address',
 'administr',
 'admiss',
 'admit',
 'adopt',
 'advanc',
 'advantag',
 'advers',
 'advic',
 'advisor',
 'aerogel',
 'aesthet',
 'affect',
 'afraid',
 'africa',
 'afsb',
 'age',
 'agenc',
 'agent',
 'aggreg',
 'agni',
 'ago',
 'agreement',
 'aho',
 'aiim',
 'air',
 'airbnb',
 'aircraft',
 'airforc',
 'airport',
 'airticket',
 'akshay',
 'albanian',
 'alexa',
 'algebra',
 'ali',
 'align',
 'aliv',
 'allel',
 'allig',
 'allison',
 'allow',
 'almost',
 'alon',
 'along',
 'alphabet',
 'alreadi',
 'also',
 'altern',
 'although',
 'alway',
 'amadeu',
 'amaz',
 'amazon',
 'amend',
 'america',
 'american

In [35]:
X.toarray()

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

Or use keras text features extraction:

In [9]:
## some config values 
embedded_size = 300 # how big is each word vector
max_features = 50000 # how many unique words to use (i.e num rows in embedding vector)
max_len = 100 # max number of words in a question to use


## Tokenize the sentences
tokenizer = Tokenizer(num_words=max_features)
tokenizer.fit_on_texts(list(X[:50]))
train_X = tokenizer.texts_to_sequences(X[:50])
#val_X = tokenizer.texts_to_sequences(val)
#test_X = tokenizer.texts_to_sequences(test_X)

## Pad the sentences 
train_X = pad_sequences(train_X, maxlen=maxlen)
val_X = pad_sequences(val_X, maxlen=maxlen)
test_X = pad_sequences(test_X, maxlen=maxlen)

## Get the target values
train_y = train_df['target'].values
val_y = val_df['target'].values

### Modelling

Data Preparation

In [ ]:


# over-sampling
ros = RandomOverSampler(random_state=0)
X_resampled, y_resampled = ros.fit_sample(X, y)

# check imblance again
print(sorted(Counter(y_resampled).items()))

In [ ]:
# split train to training and validation
train, val = train_test_split(train, test_size=0.1, random_state=24)

### Self-trained Embedding

In [ ]:
inp = Input(shape=(maxlen,))
x = Embedding(max_features, embed_size)(inp)
x = Bidirectional(CuDNNGRU(64, return_sequences=True))(x)
x = GlobalMaxPool1D()(x)
x = Dense(16, activation="relu")(x)
x = Dropout(0.1)(x)
x = Dense(1, activation="sigmoid")(x)
model = Model(inputs=inp, outputs=x)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

print(model.summary())

In [ ]:
## Train the model 
model.fit(train_X, train_y, batch_size=512, epochs=2, validation_data=(val_X, val_y))

In [ ]:
# validation score
pred_noemb_val_y = model.predict([val_X], batch_size=1024, verbose=1)
for thresh in np.arange(0.1, 0.501, 0.01):
    thresh = np.round(thresh, 2)
    print("F1 score at threshold {0} is {1}".format(thresh, metrics.f1_score(val_y, (pred_noemb_val_y>thresh).astype(int))))

In [ ]:
# predict test
pred_noemb_test_y = model.predict([test_X], batch_size=1024, verbose=1)

In [ ]:
# clean up memory for next step
del model, inp, x
import gc; gc.collect()
time.sleep(10)

### Glove Embeddings

In [ ]:
EMBEDDING_FILE = '../input/embeddings/glove.840B.300d/glove.840B.300d.txt'
def get_coefs(word,*arr): return word, np.asarray(arr, dtype='float32')
embeddings_index = dict(get_coefs(*o.split(" ")) for o in open(EMBEDDING_FILE))

all_embs = np.stack(embeddings_index.values())
emb_mean,emb_std = all_embs.mean(), all_embs.std()
embed_size = all_embs.shape[1]

word_index = tokenizer.word_index
nb_words = min(max_features, len(word_index))
embedding_matrix = np.random.normal(emb_mean, emb_std, (nb_words, embed_size))
for word, i in word_index.items():
    if i >= max_features: continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None: embedding_matrix[i] = embedding_vector
        
inp = Input(shape=(maxlen,))
x = Embedding(max_features, embed_size, weights=[embedding_matrix])(inp)
x = Bidirectional(CuDNNGRU(64, return_sequences=True))(x)
x = GlobalMaxPool1D()(x)
x = Dense(16, activation="relu")(x)
x = Dropout(0.1)(x)
x = Dense(1, activation="sigmoid")(x)
model = Model(inputs=inp, outputs=x)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])
print(model.summary())

In [ ]:
model.fit(train_X, train_y, batch_size=512, epochs=2, validation_data=(val_X, val_y))

In [ ]:
pred_glove_val_y = model.predict([val_X], batch_size=1024, verbose=1)
for thresh in np.arange(0.1, 0.501, 0.01):
    thresh = np.round(thresh, 2)
    print("F1 score at threshold {0} is {1}".format(thresh, metrics.f1_score(val_y, (pred_glove_val_y>thresh).astype(int))))

In [ ]:
pred_glove_test_y = model.predict([test_X], batch_size=1024, verbose=1)

In [ ]:
del word_index, embeddings_index, all_embs, embedding_matrix, model, inp, x
import gc; gc.collect()
time.sleep(10)

### Wiki News FastText Embeddings

In [ ]:
EMBEDDING_FILE = '../input/embeddings/wiki-news-300d-1M/wiki-news-300d-1M.vec'
def get_coefs(word,*arr): return word, np.asarray(arr, dtype='float32')
embeddings_index = dict(get_coefs(*o.split(" ")) for o in open(EMBEDDING_FILE) if len(o)>100)

all_embs = np.stack(embeddings_index.values())
emb_mean,emb_std = all_embs.mean(), all_embs.std()
embed_size = all_embs.shape[1]

word_index = tokenizer.word_index
nb_words = min(max_features, len(word_index))
embedding_matrix = np.random.normal(emb_mean, emb_std, (nb_words, embed_size))
for word, i in word_index.items():
    if i >= max_features: continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None: embedding_matrix[i] = embedding_vector
        
inp = Input(shape=(maxlen,))
x = Embedding(max_features, embed_size, weights=[embedding_matrix])(inp)
x = Bidirectional(CuDNNGRU(64, return_sequences=True))(x)
x = GlobalMaxPool1D()(x)
x = Dense(16, activation="relu")(x)
x = Dropout(0.1)(x)
x = Dense(1, activation="sigmoid")(x)
model = Model(inputs=inp, outputs=x)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

In [ ]:
model.fit(train_X, train_y, batch_size=512, epochs=2, validation_data=(val_X, val_y))

In [ ]:
pred_fasttext_val_y = model.predict([val_X], batch_size=1024, verbose=1)
for thresh in np.arange(0.1, 0.501, 0.01):
    thresh = np.round(thresh, 2)
    print("F1 score at threshold {0} is {1}".format(thresh, metrics.f1_score(val_y, (pred_fasttext_val_y>thresh).astype(int))))

In [ ]:
pred_fasttext_test_y = model.predict([test_X], batch_size=1024, verbose=1)

In [ ]:
del word_index, embeddings_index, all_embs, embedding_matrix, model, inp, x
import gc; gc.collect()
time.sleep(10)

### Paragram Embeddings

In [ ]:
EMBEDDING_FILE = '../input/embeddings/paragram_300_sl999/paragram_300_sl999.txt'
def get_coefs(word,*arr): return word, np.asarray(arr, dtype='float32')
embeddings_index = dict(get_coefs(*o.split(" ")) for o in open(EMBEDDING_FILE, encoding="utf8", errors='ignore') if len(o)>100)

all_embs = np.stack(embeddings_index.values())
emb_mean,emb_std = all_embs.mean(), all_embs.std()
embed_size = all_embs.shape[1]

word_index = tokenizer.word_index
nb_words = min(max_features, len(word_index))
embedding_matrix = np.random.normal(emb_mean, emb_std, (nb_words, embed_size))
for word, i in word_index.items():
    if i >= max_features: continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None: embedding_matrix[i] = embedding_vector
        
inp = Input(shape=(maxlen,))
x = Embedding(max_features, embed_size, weights=[embedding_matrix])(inp)
x = Bidirectional(CuDNNGRU(64, return_sequences=True))(x)
x = GlobalMaxPool1D()(x)
x = Dense(16, activation="relu")(x)
x = Dropout(0.1)(x)
x = Dense(1, activation="sigmoid")(x)
model = Model(inputs=inp, outputs=x)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

In [ ]:
model.fit(train_X, train_y, batch_size=512, epochs=2, validation_data=(val_X, val_y))

In [ ]:
pred_paragram_val_y = model.predict([val_X], batch_size=1024, verbose=1)
for thresh in np.arange(0.1, 0.501, 0.01):
    thresh = np.round(thresh, 2)
    print("F1 score at threshold {0} is {1}".format(thresh, metrics.f1_score(val_y, (pred_paragram_val_y>thresh).astype(int))))

In [ ]:
pred_paragram_test_y = model.predict([test_X], batch_size=1024, verbose=1)

In [ ]:
del word_index, embeddings_index, all_embs, embedding_matrix, model, inp, x
import gc; gc.collect()
time.sleep(10)

### Ensembling

In [ ]:
pred_val_y = 0.33*pred_glove_val_y + 0.33*pred_fasttext_val_y + 0.34*pred_paragram_val_y 
for thresh in np.arange(0.1, 0.501, 0.01):
    thresh = np.round(thresh, 2)
    print("F1 score at threshold {0} is {1}".format(thresh, metrics.f1_score(val_y, (pred_val_y>thresh).astype(int))))

In [ ]:
pred_test_y = 0.33*pred_glove_test_y + 0.33*pred_fasttext_test_y + 0.34*pred_paragram_test_y
pred_test_y = (pred_test_y>0.35).astype(int)
out_df = pd.DataFrame({"qid":test_df["qid"].values})
out_df['prediction'] = pred_test_y
out_df.to_csv("submission.csv", index=False)

### Reference 

- https://www.analyticsvidhya.com/blog/2018/04/a-comprehensive-guide-to-understand-and-implement-text-classification-in-python/
- https://www.kaggle.com/sudalairajkumar/a-look-at-different-embeddings
- https://keras.io/preprocessing/text/
- https://machinelearningmastery.com/prepare-text-data-deep-learning-keras/
- https://towardsdatascience.com/finding-similar-quora-questions-with-bow-tfidf-and-random-forest-c54ad88d1370